# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [2]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests


# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
#vacation_df = pd.read_csv("../Vacation_Itinerary/WeatherPy_vacation.csv")

# Import the WeatherPy_database.csv file. 
#city_data_df = pd.read_csv("../WeatherPy_vacation.csv")


City_ID          City Country  Max Temp   Current Description    Lat  \
0        6      Cidreira      BR     72.01      scattered clouds -30.17   
1        7          Hilo      US     75.20  heavy intensity rain  19.71   
2       14  Puerto Ayora      EC     78.80            few clouds  -0.74   
3       17         Kapaa      US     82.40         broken clouds  22.08   
4       19    Rock Sound      BS     84.43       overcast clouds  24.90   

      Lng                            Hotel Name  
0  -50.22                         Hotel Castelo  
1 -155.08                          Pakalana Inn  
2  -90.35  Hostal La Mirada De Solitario George  
3 -159.32                     Coral Reef Resort  
4  -76.20                       Rock Sound Club

In [11]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/WeatherPy_vacation.csv",encoding='utf-16')

In [13]:
# Display sample data
vacation_df.head()

Unnamed: 0       City Country  Max Temp Current Description      Lat  \
0           6   Bengkulu      ID     79.84     overcast clouds  -3.8004   
1           9      Tabas      IR     81.59     overcast clouds  33.5959   
2          17  Mahebourg      MU     80.26       broken clouds -20.4081   
3          18     Avarua      CK     77.05       broken clouds -21.2078   
4          20   Benguela      AO     78.33     overcast clouds -12.5763   

        Lng     Hotel Name  
0  102.2655     Dena Hotel  
1   56.9244       هتل امیر  
2   57.7000  Grand Bel Air  
3 -159.7750   Paradise Inn  
4   13.4055  Hotel Moibela

In [14]:
# Find the column names 
print(vacation_df.columns)

# Rename the columns 
vacation_df.rename(columns={"Unnamed: 0": "City_ID"}, inplace=True)

# Check columns renamed correctly 
vacation_df.head()

Index(['Unnamed: 0', 'City', 'Country', 'Max Temp', 'Current Description',
       'Lat', 'Lng', 'Hotel Name'],
      dtype='object')


City_ID       City Country  Max Temp Current Description      Lat  \
0        6   Bengkulu      ID     79.84     overcast clouds  -3.8004   
1        9      Tabas      IR     81.59     overcast clouds  33.5959   
2       17  Mahebourg      MU     80.26       broken clouds -20.4081   
3       18     Avarua      CK     77.05       broken clouds -21.2078   
4       20   Benguela      AO     78.33     overcast clouds -12.5763   

        Lng     Hotel Name  
0  102.2655     Dena Hotel  
1   56.9244       هتل امیر  
2   57.7000  Grand Bel Air  
3 -159.7750   Paradise Inn  
4   13.4055  Hotel Moibela

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [15]:
# Configure the map plot.
map_plot = vacation_df.hvplot.points(
"Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    alpha = 0.5,
    color = "City",
    hover_cols = ["Hotel Name", "Country", "Current Description"]
)
# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [16]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method.

vacation_start = vacation_df.loc[vacation_df["City"]=='Cozumel']
vacation_end = vacation_df.loc[vacation_df["City"]=='Cozumel']
vacation_stop1 = vacation_df.loc[vacation_df["City"]=='Puerto Escondido']
vacation_stop2 = vacation_df.loc[vacation_df["City"]=='Pochulta']
vacation_stop3 = vacation_df.loc[vacation_df["City"]=='Parrita']

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [17]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start, vacation_stop1, vacation_stop2, vacation_stop3, vacation_end], ignore_index=True)

# Display sample data
itinerary_df.head()

City_ID              City Country  Max Temp Current Description      Lat  \
0       72           Cozumel      MX     77.95       broken clouds  20.5083   
1      168  Puerto Escondido      MX     81.43          few clouds  15.8500   
2      342           Parrita      CR     80.24          light rain   9.5201   
3       72           Cozumel      MX     77.95       broken clouds  20.5083   

       Lng             Hotel Name  
0 -86.9458   Hotel Isla Esmeralda  
1 -97.0667       Hotel Barlovento  
2 -84.3225  Hotel Paraíso Carlisa  
3 -86.9458   Hotel Isla Esmeralda

# Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [21]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[["Lng", "Lat"]].copy()

# Display sample data
waypoints_df.head()

Lng      Lat
0 -86.9458  20.5083
1 -97.0667  15.8500
2 -84.3225   9.5201
3 -86.9458  20.5083

## Use GeoViews to create map that shows the four cities in the itinerary

In [22]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Current Description"]
)

In [23]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Current Description)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [37]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [38]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': 'bf07e5e2a49b4154aab21e7584517025',
 'waypoints': '20.5083,-86.9458|15.85,-97.0667|9.5201,-84.3225|20.5083,-86.9458'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [39]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [40]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [44]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = [] 

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for leg in legs:
    
        # Loop through coordinates in each leg and extract latitude and longitude 
        for coordinate in leg:
            # Append Longitude list
            longitude.append(coordinate[0])
    
            # Append Latitude list
            latitude.append(coordinate[1])      

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [45]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df['longitude'] = longitude
route_df['latitude'] = latitude

# Display sample data
route_df.head() 


longitude   latitude
0 -86.945966  20.508121
1 -86.945604  20.507826
2 -86.946307  20.507005
3 -86.947124  20.507665
4 -86.947951  20.508345

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [46]:
# Configure the route path by using the GeoViews' Path function

route_path = gv.Path([route_df]).opts(color='red', line_width=3, height= 500, width=800)

In [48]:
# Display a composed plot by using the route_map and route_path objects

waypoints_map*route_path

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Current Description)
   .Path.I   :Path   [longitude,latitude]

In [ ]:
# Save your map to the Vacation_Itinerary folder as WeatherPy_travel_map.png